The goal is to compare the temperature and salinity from the glider with the measurements obtained with the research Vessel CTD at the same time of the year.

In [1]:
from bokeh.plotting import figure, output_notebook, show
import cf
import numpy as np
import pysocibclient

Data URL's for the glider and the CTD. We consider data for April 2015.

In [2]:
gliderfile = 'http://thredds.socib.es/thredds/dodsC/auv/glider/ideep02-ime_sldeep002/L1/2015/dep0007_ideep02_ime-sldeep002_L1_2015-04-22_data_rt.nc'
ctdfile = 'http://thredds.socib.es/thredds/dodsC/research_vessel/ctd/socib_rv-scb_sbe9002/L1/2015/dep0009_socib-rv_scb-sbe9002_L1_2015-04-23.nc'

We configure bokeh to view the images within the notebook:

In [3]:
# output to static HTML file
output_notebook()

Loading BokehJS ...

# Load data

The data will be obtained using the cf-python library.

## Glider data

In [4]:
f = cf.read(gliderfile)
tempGlider = f.select('sea_water_temperature')[0].array
psalGlider = f.select('sea_water_salinity')[0].array

We also remove the data points with too high salinity of temperature.

In [5]:
goodvalues = np.where(np.logical_and((tempGlider<35), (psalGlider< 45)) )
#tempGlider = tempGlider[goodvalues]
#psalGlider = psalGlider[goodvalues]

## CTD data

Note that with the CTD, the salinity has *sea_water_practical_salinity* as standard name.<br/>
Also, as there are actually 2 sensors measuring temperature and salinity in the rosette, we compute the mean of the 2 for both variables. 

In [6]:
f = cf.read(ctdfile)
tempCTD = 0.5*(f.select('sea_water_temperature')[0].array[::]+ f.select('sea_water_temperature')[1].array)
psalCTD = 0.5*(f.select('sea_water_practical_salinity')[0].array+ f.select('sea_water_practical_salinity')[1].array)

# Create the figure

We only represent one point out of 50 for the glider (one out of 5 for the CTD), otherwise the plot visualisation can be relatively slow. 

In [8]:
p = figure(title="T-S Diagram", x_axis_label='Salinity', y_axis_label='Temperature')
p.circle(psalCTD.flatten()[::], tempCTD.flatten()[::], size=1, line_color="black", fill_color='black', legend="CTD")
p.circle(psalGlider[::], tempGlider[::], line_color="blue", fill_color='blue', size=1, legend="Glider")
show(p)